# Setup

## Hands-on: Partitioning, Gate Fusion, CNOT Decomposition, and OSR

This notebook follows the lecture:
- Visualize and export quantum circuits as SVG
- Play with simple partitioning and cost models
- Explore CNOT-only linear reversible circuits (GL(n,2))
- Measure entanglement using Operator Schmidt Rank (OSR)

In [ ]:
%pip install pip jedi qiskit qiskit-aer scipy sympy pylatexenc tbb-devel tbb PuLP gurobipy --upgrade
%pip install setuptools numpy matplotlib requests
import os, sys, sympy, functools, operator, itertools, base64, zlib, requests, timeit
from IPython.display import Image, SVG
colab = 'google.colab' in sys.modules
if colab:
  %env TBB_INC_DIR=/usr/local/include
  %env TBB_LIB_DIR=/usr/local/lib
else:
  home_inc = os.path.expanduser("~/.local/include")
  home_lib = os.path.expanduser("~/.local/lib")
  %env TBB_INC_DIR=$home_inc
  %env TBB_LIB_DIR=$home_lib
%pip install squander --upgrade

# %%
import numpy as np
import matplotlib.pyplot as plt

from qiskit import QuantumCircuit
from qiskit.circuit import Parameter
from qiskit.circuit.library import GlobalPhaseGate
from qiskit.quantum_info import Operator

def file_to_compressed_base64(filename):
    with open(filename, "rb") as f:
        return base64.b64encode(zlib.compress(f.read())).decode('utf-8')
def compressed_base64_to_raw(base64_data):
    return zlib.decompress(base64.b64decode(base64_data))

Visualizing a 3-qubit circuit and exporting SVG

## Part 1: Visualizing a 3-qubit circuit and exporting SVG

We'll build a small 3-qubit circuit that we can also use in the slides:
- layer of single-qubit gates
- some entangling CNOTs
- a barrier to suggest a "partition boundary"

In [ ]:
qc = QuantumCircuit(3, name="Demo3Q")

# First "block"
qc.h(0)
qc.rx(np.pi/4, 1)
qc.ry(-np.pi/6, 2)
qc.cx(0, 1)
qc.cx(1, 2)

# Visual partition boundary
qc.barrier()

# Second "block"
qc.rz(np.pi/3, 0)
qc.cx(2, 0)
qc.rx(-np.pi/5, 1)

circuit_text = qc.draw(output="text", fold=-1)

fig, ax = plt.subplots(figsize=(5, 1.75))
ax.axis("off")
ax.text(
    0.01, 0.99,
    str(circuit_text),
    family="monospace",
    fontsize=10,
    va="top",
)
fig.savefig("demo_3qubit_text.svg", format="svg", bbox_inches="tight")
plt.close(fig)
# (Instructor) Text-based SVG used in slides. Students can ignore this output.
print(qc.draw(output="latex_source"))
circuit_text

Let's draw the circuit using Qiskit's Matplotlib drawer and save it as an SVG.

In [ ]:
from qiskit.visualization import circuit_drawer

fig = circuit_drawer(qc, output="mpl")

# Save as SVG
svg_filename = "demo_3qubit_circuit.svg"
fig.savefig(svg_filename, format="svg", bbox_inches="tight")
print(f"Saved SVG to {svg_filename}")

display(SVG(svg_filename))

### Exercise 1: Customize the circuit

1. Add another entangling gate (e.g., `cx(0,2)` or a controlled-phase).
2. Insert a second barrier.
3. Re-run the drawing and export another SVG (e.g., `demo_3qubit_circuit_v2.svg`).

Hint: Use `qc.barrier()` and regular Qiskit gate methods.

In [ ]:
SVG(data=compressed_base64_to_raw('eJzlXetzHEmR/+6/opndD3DH9NT7IWQTh5fjiFiONxwXF0HMSmNbIEtGGu962eB/v/xlVXdnyT22NBotApYIXJVdnZVZmZWvqh4d//Dd6/Puy83V9dnlxdOF7tWi21ycXJ6eXbx8uni7fbFMi+56u744XZ9fXmyeLi4uFz989uT4O5/9/Plv/vCLH3fXX77sfvHbH33+0+fdYrla/d4+X60++81n3a9/95NO93q1+vF/L5503eLVdvvmaLX66quv+q9sf3n1cvWTq/WbV2cn1ysausJQem1F6LTuT7enC5oEuIm8i+ujd+dnF39+OoNE55xX/HTRfXV2un31dOGd6wPgb7aL7tXm7OWrLTEWTa+U9TkB+uXZ5qsfXb57ulCd6sbx3TRoUeadm9EopUDmQq6aJnK749eb7fp0vV1Tuzu+On1x9KvP/rMycHoy4nrz9uqcMZ2erDbnm9ebi+01818nPTqZxp5cbdbbsy83J5evX19eXPNrF9efDCNpjp2LoszKmCWNWF5/fbFdv1viPVDWHZ+cHP3+8urP3OmOT0+Otl+/2XQg+Gpzffn26mQzS+zpyeszjFz9ent2fv7T1+uXm8VqQkKcb54ZZfxS66X2v9HmyOgjWlxrjQ3+eDWMGd94cXn1er19dgZMWNJ/J654WH0wDuRluLwqAKb/P17SstV+YeFse7559rP19s355fb87IvuS9vn3n2/AyPXxMnr8RHzw/OUlyrWVYuWB8iJecCwbserKl/IfSUEf3y6eXHNI663X59vOizY08V28267Orm+Xjz7t2+ut1eXf94sSWc3f7o8uzjqri7fXpz+oBPwk/Wbo+6Lt9vt345XjIZnqZiPX3Znp08XL85evr3a/JE1b4C9WW9PXlVQd0y9Vx1Bf0ZKPql29+TzWZVv4Qpd7I4nf30CA0A0YMrz86Pukxf8XxH98eqlmH/9bnM9Tl9AYMecDkBJVKC5VNY5dDSrSdYwBdb0MTmfJ+CiOzk/e7PEi2SRrs6/+8mbpDZ+Y9dJv/jeDeIuyEgNS0mkKv5vXFu2EEedeX+xr//ydn01qHNl6gYL5kMsZNUHG2npWiYE+LGwYT/Ehrahz1nrqg4jHxL+d2ekaPmMOHzuc7Qxx86QPVWBNWqpVU59ikGntBuuQu+N0fQq+J7wCPhf78Z53SaC+RYwMK9737BfbAJZ2s3VB+Xo3udfW09Sctbf0EcBP9CuMqf55DDq6GfYSKa3Llnvb+ijeHCwjXU4TsL7nFjSN6fJvNobnIgHj04icYaPEPsYSIHMTT6mB4+Hj2IfZuwc7eM+BApHXEd0u6Dq/jCWuHDapt1wYTgElhF6V9uwTvjfD7rLN+sTiqmOOlLnDzEzs9kFGVrbPmn3PtU7H7Rszi7LQ7M0s/ElS0H1OqSqZpKlnQ9aXudX56GZmrEBTvlexWyNaVfdGdtrH23aDRdKJ7B8a0o3YwgEGe16C6p3PmjZnF2Wh2YpfZilRrckSzsftLzOr85DM5XfZyq63kdvVUAsQy7TuBIIKNdH5d0H4Cb3RiftAZ6wTNA7R0Frd+qDjIIawN5RUE111Id41ySPqMz7TO58ED29a3SBT4gE+K785xc6eSv4bwH35X8mrxL8e0rufDAu3eR/5wMyLtkEXR4ITAL+yFZgJg+Q8S6F+MpE7bonzwkee51Ndl7AyXnQTjBBMdCa4DXBMg1UhKdzZJxiyjEzAqd6ZWMIhDhQAKodLQiAnrDEzvneJU2jJWwIi55LoO1VckE3CGmFrcs3Ztc0MLryuiBU9cbmhIkmluitGGxIXvI/ARkDCTp7mq4ZbPtAtKjYoKXMLycaeoMEItKTvviGXIplo0tOC74ETCyAgE5LJXBOayrmbwQgiJ2ENXIlpTqnAndV3TYc3Rmf7qu6MyGqoFsrcvTJROsG6cdMjt/JB+RhaHVsUJRgKFKlqJGskxic1zpSmpR6lZ3SqegfLbohWVJ6GHqtg3ORgJThktBzl+kta7NqYFOa9VyAU+yTUy5LlMnDKbJCTPMn8pRJ2Tr9SGvSvVEmqSTZSkR/1iE0wpuAVfqUigciWw7GriIFShKtSUQq2a7QkmCIA59z8JJcQzy4lIwWfE2wdgkEfFquCatY14mCVggTuUJiE2NSuPO68EBKbPZS4bkqhMjSschhsL4kCe9Cdk7AdXJ9yCEoAlIrKa9oOUg43jkYQFplMh7D7k+ht5A6wU1P5oFNBQFTiGRVs6axPqYG1khvBKdMwkswVBPKlMhQpezl9KQQ1KAwrrw+0kpv+WzZUk5cJQg/BuQi0xJMQMZAYnQZpkoOJjVQivaARBvJB3jj400aIpk9WiQn6Y2kttR0gq0R1C7ABJ7WasIoFnWa/oYERlqluEaupGDntOCRGeCPFJ/I9dD+jdYW1okN51Ww8oGGyTCRDTCZR2e8Z6XI5HO8jrDQDhZD6chIaN0jjSd7qZ0hc6gcmrTwieSe2fWTfrJVEcCp5PK8gTuyGg7mSqAld0q2lw2boIICeG+dHaQ4EW2IFU+CjA2DZNGc8wFNsR4TlHWJUHoydqEZHrHFsmazOKGmSDJlDWN4g5JIKkdMsx2fCI8aLhv51cSigDXLIeDT2gm0YpkFFa1UBNFCiIJBKfBZ/XhURnmmCmFQ06YlIdvVZH6G7AMF945UYRdcZoQCzf4pobVf6KYw3gLuu6lnyhaC7Db1E2zufNDkhALT400KZ6ocshLtsNEo8OBtbI3pg0qZAnzxwBrbR5+CKlBlHQy9NTgoChrbgHIF8p05poKEwiLaCjAAtAspLEIIBCilJimUMI/MEfxNA5U7uXlAsqB8k+cUqGl6R7lOSwnFThTHVf8oCaccIlPqwHNOTFrYAx2SbavzI5SRUCIE7+ya4Tr3KhitXINakxsmsxnfo0THnoyDci3hmkxNVsm2TEposybywbSEEvW03IKSVjqCcCnMiUkp+Fk9eWR+e6biJQj3DkFOzZugKUZFFEwnOCWOPYVOQenOk8woU8F6JASH5Do6T97UUZRT5EgBe6L1pQDPIWk2vNactHooADkBFTPJqAFOSa+EEokpuKwlUov01GZvJAWkBMkEW/fFSCzpUaLso27Fyha0DiUEL9dgArICpJ72SkCRYBqsabtZTWZPotWWiCUEriVBEw+0SJhtIlcTD4Gy+IYxARRrIKDTck1IxcJOBLRSmKidJDaxJUU7pwePyT2bmZqlPEeTFSsbUk8LBMM1wW2k3U0xFynEWAQBDCpC690UTCyHRxHmc6quWAqPSDSka6IOI4FCcgI6FHckzrEKJAkQFSNJ61hdElxNdSixBE3Rikx/74MnQDOY6NaB5NygdTQywQA2JARSGFg/I8klIClcspIvARMrIKDTYgmc07KK+RsZCGJHeU1cCcHOasHjsr1mpuIsj4ebnAnS98Q4VzrHBzZiRTkKH4NtS9GUgTsyN2JzG1HgJFlaGcpbTlpJ6lGG/Q20caPywZBRSMxT7iEJaVKVieopr5H8TTmQXI4mZYKC5ECPXDscW8zDtEnUQRHJ0SPCaenw0KEMsynJ9hHhOCys4FACm/WQD6blE5jFUgtCWskIuoUgBY9C5PMa8qjM8sxBgiND5ZOzZL3aIxOXEzkh5z74oDlLkajucZjysLmTmalIO49CZik4NCmSV8SqJ6dsdj9ocieB6dHmTmamoCnobnJkwecuuMydBZr9c+eH4r7e/ZnJHOWlsoA7FUbfvFSGuqgmk3nPy1jz9+P2u8Q0kyHAjGZK5OzN23Fk65RRNh7sVtkhGZk74W5qUBS9kLPSNy/I4ZwhU6QR73lj86C8zMQOqL1Rem7t+5f9yBuRc47tg0fDy4y7kLkHnGauW0XmZZSj+6gfEyMzNh/ZliVnZa28m20pOqEAyMYDXVo8KBczdrsJOuQ2aa4zPsJtMnMsYQNlwzZZ+95N0oiiE1kv87i2Cb54mG79v/wwOc/qJxjfWS67T7/5y9/++I3626fdcjnAX3bbq/XFNT4LIcxonq+3m+/aSJtMUZqFdInyfLIl3+uuT9bnm+/ivpbx3bL8O84wfZ7RTQsMcj/b/Gn9u7e/JszLn39xfvaXt5tl1ItaPQ6BPD9he/LLjjKA1Bm+hWdsFximUTlZZuQ4JnGDgKAKTZ89IYj8bnYdiMK/2pAxqDAuZlBYTXgtv4vrICZyTRolOQXlpGmMRY0Jl8u8VZ11BQPZfIPQHbdRUU5CC4i91RUcEypHBbVVABOoQ85K04dqofCqI2LQYYy1Y1C4WlKmUa+QgtWxNy7MX5/8jDjGXQybCvc4TCfLrXDZ1BZCeVYMQnJgyzIhC+E2WUXTkfKWRcGRNyjmlsFNggFseAWjj0RZqJxyLQgnFYwMLUyXdSgdjVNWk2NgMJaN0haFE3qaIKgC1orW3xI4Q2CqQJkl5GgTbwjYhDIO2qa0Zz1bfVi3rBp0SlnXUcqkeHLvYulo5AeUmBawwgUeg6nRMtakEUx7PZfRqHyMOEg6BbPKZWmML0CgrCPppfo+twa03OHZePBAREEB2gTJEHfpxsIBLWUuHWvgNCjWYpy40WC52ozWOBVfdNDDaF8GMw5sGcZct5HGfGgnCtvqQMf3KwmOxoDT8S6gmTBwmJ/fZrIEtbeV4PjBVem9vd50/KHh0aurzYuni0/mTcbqVi9AD2ZNWrCUdweihHYZ5dQKJI0mLU7UDdZ2Mrsz5tfsbX713cxv9r1KibbpAcyvHcxuJAMEI1biWt+0Sae5AyNpE5nL2nbO1UHQx1AeGActkJ2KikJl3bT5qzfMOzb46aPQGP1taIzdW2PM3TSGL4M5cyCVMYshxSNjMArU6qatShkmTw1ffGKilzJf4MDNl8EaKRpgNOwukJrq2Nitkj8nCMq4ZC6LD4o4tIFNKi1bXHbpsP3x5Npsrr6ZzRKSA50IHbfYhLOBBdgoamldnFCEvmvkFGQwE7zb59wuyk4DEu5TclChUY+mOYtDqBZPj8aZGRjA5BEJMa6jwiTj9q9TxpeWdYWk0tEcM1BYidMUBmuY6QDvkXE73IRQLDhWCt7awOloLsDDE7P3BGSUz6PYUubb2FJujy31Xx/fSsn10ZN+8llDItuXothJlveRvdMucqnuokBCGswledDcdij2Yg20HoGU7AzDnCY1bzpqHDO1DKLoEans8BgQMTYKsgfQGeL5TsL0+9jH/3tz9unKNSKd/aB6h6Btbyl6qZdAU6JML0+SVgmSVmmvDMeeDOEo8gQLmwLpZOQZQydxwmK4gmn5S7jaodQhdHGIzEl8nm0K2yJVUw3gwZ0CBIAlW7EGMS0fUMPWhAK0GQceuZgdpLI8Gb2+dK68RfiXoBHx/LJG+DzZUiMIRAjALU7R8gC2CZeCi8kF6fjS13IwWb4e4098Kz9kvMPYwRJUVVWlkXUen7poxva0cvfLDMyLwYfBC47RChzQ0IHhXPqSlqmxJcbfMzdxQ24CKRTv83kH+fMUHDvBN8lOGcXpgBEWwCokI7IzvGVxnaTt6KppPEx21DjN1BoHyDfRjqqkpBMZD+hieOPM7lbSll5lcvnfu6UTMrv2fVC9UR65/x0xQo6zGHGTNwcHe3wT462MX9jL+L2mUVevv/nVH//nRoR4Fxuo+6jZBqbcR+VS1Pd0dn4IGQ2+RuHCAZss1EQ0jJDBSW/KxfygrqNR7LABuaeJxQyYMDq0wcmRTaKh/HsBCP9gtbma420ucRjAXMPJqNhl6HyOk+9rOrscIU2jRjVH2DV0rMG+s7XUExxCTjataNliHrljUqkJgbJcrDVqT8aiCjKtCDZ2iQC0i5OzdiX5YiJKB3Glqk8Mwj4TVTHGCDIpSralNRBROtHW0eRy8oiE5yoMyllL534mzg8hDu51jlGNgs8aFtaA+TykDWqyvk6JqMZwYc1VdyBCHHpB1e+PKR7neJ9sKMmUoQibSyMhsajrOBHzACbL7wpy72ypsHizmKLqnc2oqyFctvo+0XLcx8YsPy0xVtjXvkScDJYYy6XeWErb0j1jLEO52BBPI1s0ZV87rkXKDmVJrAUYJdtl0D1dehisnMYOrKVhHRAHoaNJbjRRLgVTTuoUEmHNxexixLiTcx0clR5RcGERiMdqo63AmMIw0qLwhte5MSDlDs/FYwcSGEPZWxPBMELW4us+H0qyYfkDxmqyNcwiV29TQuXPF1pQY+Zc2vAmHlJs1MJLiu34ss/Ao+GkHQVr2CtfrFTNd8C7t4gUi5UiO07zK6YSNUxVs3qYYe5YSo1RHyiswm9wZZ9b4wqgE1ERL6V325ZAwf5QArWqtFEIGEqgQwHVibIq3590WG7SHJJD4QHzlXzfgvehDBCGmoDB90IuqprYsy1CjD6t+ANYpbI7dtolkpK5tV36eFBGKVRMGXdl74h6Z3CG80RSak3b9Y4osSXnUcbYh+RRxn8P5a1MZ7pfePaHe4RnpteqmE8beuXTAeKzXC3XUk+eunx3Xb125r1ZAgTeQ2O+gWR08ufI1Wp1gTvF/4YhwePWMGCa7HF74vywnng4h577jsgk3PSyvv1JnAkqfsxj7zPo5en6+tX66mr99VFHW/f7ug/No8sXL64326NOiUPr8stiHz5Xn/syaJbyhiP5Ux6PjqWZC1s7SG95Ej9o8mh4YiuW966w2Y8XTU3APYGAFfC+J196/1qatYvxG7OIMn8o8Q08K1ez+Fs5CjAYjKNqnVBT5xZM5gDm/I2DilKR5w+D+FZBFMehKPkzkKKCblkO1hE0oAaEzLPEj2hWR49/QBlvVV+jIEQ6wKSjDl09ReCjfbRNMIo2Qy3sWXwBn0tjoLd0IuKagFxPqYqBy7oI8xIbVVsKVLjj0HZq1VinMJSQf1miGO7wZ8dDsGX4MoJGFbJcS6iEcSchivT4NkGZQhlqQcPJShInKzENJysIgnRgcSA9c/iWGal1CShrmu3L4gFE0RCfy+PDClXO5XHwUU9WspMhla1n4Lhk4ZwpIRWfPiqk4WiR7ukRbDWXR8E4gldWHFQhA0t01Ke/WyXrMMGSrGTdLVayt6hk7RMqTZcq94uV/vc2h52GHIo2bGwoWrRepWjuGxWtq7Gx4lSGT+3aji51B05m6hEoa6Bsq3q7Z2rgBJyDKewcXfYrTyTb/wDR0fpbqFPova62DYUKv2+kTUllbyPr1MFOg6wf6hR5qoNZHfKNjh4s+M2OyYNzgmPDqY/2DqlwGGoFung2LoCO6XJQNXe2fLspDL5Q23Lkzq0xXUaHP5dEidZWaw9HUVwkzocGKuolPI0best6RE4TE9XI5Ms5AZqxHC7hDMvzJSs0iv8WHrJ6xfHYHh7SB9/FeiEQlVTKfnJtVXpLBw6GBxuKPEYUBsefjJhb5VJaqGCc/JuKJHN9lSaEZLhqDP80Sunbz8vvtA/vlpcf5tCkycvvdmrib5OX73Nsove6hnWQcxPhgm53cPLPUUkekqOZj0BINXpNsaFvf11zgj7i/HXuw+F5yhuOHnP+Ovc16Q7SW54ebf6q97pCx1FB/HhM6fADTilb/pW1A51U2DhcAhFxpH2/Y8uPo/OVtVI600M5zfCP79WYgAfL9r/2aXzc5fxIg909TuP1PhfL7prDUDrbR1307Xal3X+mGP8et72+/15jXx/ufO6DKyI4VMhvToY71hSOxnqPCCd3so2bWji8xocsHCqXqHlol1utYWjym/e8AqX+RU3EHhd2PkLjya5g1sfe64w6wF1R7lpA/MocpXrh7iH3x4VD6UhBeTAhGfxGaE64qHwoKVkKS3JWKHAeSkz4vYqgLWqVhxKT02QZlcLtx4OLyTnT63RAKXllepuNP+Be8nBfiW/g7+lv97n+9tu9rT5pQMpG87dnB7ryNtR5vLhTyrc7mg7Hd8O9D74bRWEKfsmhQCN/o4C7ta40yod55WMsvqdbR9pSbeF7ZtlVtJ+XznQ5XNxp446upwHcwUU0GyJ+7sXXa8Cl3sOTj/UeX89JFP8iC4/0/KsEmv/V9bRhYvshypf+jtq010WnNqQwB4ktYuDY4nbnYf/4Rwq38bV3o/FWvvZuKG/law98SUb62sMIqfG1d5PSrkQBvxlngy++9jBispHcN4g8nJicCn0kq5MfQEzOph5m6mBS4l8sCtEfcC/h78Y5n/L+53P73GU6hK+93UHdPR1B+af+//jnIsHnLwa3LZisf03xanOy7d49XcSe9sbX9d/hL55a/JRnzln8vVMyPqH8KdP6dxoH/M+mPyV5jD+6+ezJ/wP1ovnp'))

In [ ]:
# TODO: Modify the circuit below.

qc2 = qc.copy()  # start from the original

# TODO: add your gates here, e.g.:

fig2 = circuit_drawer(qc2, output="mpl")

svg_filename2 = "demo_3qubit_circuit_v2.svg"
fig2.savefig(svg_filename2, format="svg", bbox_inches="tight")
print(f"Saved SVG to {svg_filename2}")

display(SVG(svg_filename2))

file_to_compressed_base64(svg_filename2)

### Segue: symbolic proofs of standard library circuit decompositions using `sympy`

First some definitions including symbols, needed trigonometric rewriting function, applying a gate from the left, and compiling by applying many gates, along with every standard library gate and SQUANDER provided gate.

This is needed so we can decompose any gate into CNOTs prior to partitioning, as we want to partition circuits with only single qubit gates and CNOTs.

In [ ]:
theta, phi, lbda, gamma = sympy.Symbol("θ"), sympy.Symbol("ϕ"), sympy.Symbol("λ"), sympy.Symbol("γ")
alpha, theta2 = sympy.Symbol("α"), sympy.Symbol("θ2")
little_endian = True
def force_euler_pairs(e):
    # replace 1 - exp(iθ) and exp(iθ) - 1 with ±2i exp(iθ/2) sin(θ/2)
    a = sympy.Wild('a', properties=[lambda k: k.is_real is not False])
    e = e.replace(1 - sympy.exp(sympy.I*a), -2*sympy.I*sympy.exp(sympy.I*a/2)*sympy.sin(a/2))
    e = e.replace(sympy.exp(sympy.I*a) - 1,  2*sympy.I*sympy.exp(sympy.I*a/2)*sympy.sin(a/2))
    return e
def quantsimp(x, rewrite=False):
    x = force_euler_pairs(sympy.sympify(x).rewrite(sympy.exp) if rewrite else sympy.sympify(x))
    return sympy.simplify(sympy.trigsimp(sympy.exptrigsimp(sympy.together(sympy.expand_power_exp(sympy.powsimp(sympy.nsimplify(x, rational=True), force=True, deep=True)))), recursive=True)).doit()
def quantsimprw(x): return quantsimp(x, rewrite=True)
def apply_to(psi, num_qubits, gate, gate_qubits):
    """
    Left-apply a k-qubit gate to designated positions inside an n-qubit operator.

    Embeds the k-qubit `gate` on `gate_qubits` (indices in [0..n-1]) under the
    current endianness, and returns (gate ⊗ I_rest) · psi with the correct qubit
    wiring. Works for psi as a full 2^n×2^n operator (not a statevector).

    Args:
        psi (sympy.Matrix): 2**num_qubits × 2**num_qubits operator to transform.
        num_qubits (int): Total number of qubits n.
        gate (sympy.Matrix): 2**k × 2**k unitary to embed.
        gate_qubits (Iterable[int]): The k target qubit indices where `gate` acts.

    Returns:
        sympy.Matrix: New 2**num_qubits × 2**num_qubits matrix after applying `gate`.
    """
    pos = [(q if little_endian else num_qubits-1-q) for q in gate_qubits]
    k = len(gate_qubits)
    deltas, combo = [1<<p for p in pos], []
    for u in range (1 << k):
        m = 0; x = u; b = 0
        while x:
            if x & 1: m ^= deltas[b]
            x >>= 1; b += 1
        combo.append(m)
    pos_set = set(pos)
    rest = [p for p in range(num_qubits) if not p in pos_set]
    output = sympy.zeros(1<<num_qubits, 1<<num_qubits)
    for rest_bits in itertools.product((0, 1), repeat=len(rest)):
        base = 0
        for bit, p in zip(rest_bits, rest):
            if bit: base |= 1<<p
        mat, idx = sympy.zeros(0, 1<<num_qubits), []
        for u in range(1 << k):
            idx.append(base ^ combo[u])
            mat = mat.col_join(psi[idx[u],:])
        prod = gate @ mat
        for u in range(1 << k):
            output[idx[u],:] = prod[u,:].applyfunc(quantsimp)
    return output
def compile_gates(num_qubits, gates):
    """
    Compose a list of embedded gates into a full n-qubit unitary.

    Args:
        num_qubits (int): Total number of qubits n.
        gates (Iterable[tuple[sympy.Matrix, Iterable[int]]]):
            Sequence of (gate, gate_qubits) pairs. Each `gate` is 2**k×2**k,
            applied to the provided `gate_qubits`.

    Returns:
        sympy.Matrix: The resulting 2**n × 2**n unitary product.
    """
    Umtx = sympy.eye(2**num_qubits)
    for gate in gates: Umtx = apply_to(Umtx, num_qubits, *gate)
    return Umtx
def make_controlled(gate, gate_qubits, gateother=None): #control is first qubit, gate qubits come after
    """
    Build a 1-control controlled version of `gate` (control is the first qubit by convention).

    Constructs block-diagonal diag(gateother or I, gate) and applies a permutation so that,
    under little-endian, the control is the least significant qubit.

    Args:
        gate (sympy.Matrix): 2**m × 2**m target unitary.
        gate_qubits (int): Number of target qubits m (excluding the control qubit).
        gateother (sympy.Matrix | None): Optional block for the control-off subspace.
            If None, identity of size 2**m is used.

    Returns:
        sympy.Matrix: A 2**(m+1) × 2**(m+1) controlled-gate matrix.
    """
    res = sympy.diag(gateother if not gateother is None else sympy.eye(1<<gate_qubits), gate)
    P = sympy.eye(1<<(gate_qubits+1))[:, [2*x+y for y in (0, 1) for x in range(1<<gate_qubits)]]
    return P * res * P.T if little_endian else res

def gate_to_latex_matrix(name, params, M, Mdecomp, circs):
    mathsyms = {"θ": r"\theta", "ϕ": r"\phi", "λ": r"\lambda", "γ": r"\gamma", "α": r"\alpha"}
    for c in circs: c.assign_parameters({x: mathsyms[x] for x in mathsyms if x in c.parameters})
    spsyms = {theta: sympy.Symbol(r"\theta"), phi: sympy.Symbol(r"\phi"), lbda: sympy.Symbol(r"\lambda"), gamma: sympy.Symbol(r"\gamma"), alpha: sympy.Symbol(r"\alpha"), theta2: sympy.Symbol(r"\theta_2")}
    return "\n".join([fr"\[ {name}\!\left(", ", ".join(mathsyms.get(str(p), str(p)) for p in params) + r"\right) = " + sympy.latex(M.subs(spsyms)) + r" \]",
                     r"\[ = " + r"\cdot".join(sympy.latex(x.subs(spsyms)) for x in Mdecomp) + r"\]"] +
                     [c.draw(output="latex_source", fold=-1) for c in circs])
def make_inverse(g): return g**-1
def make_sqrt(g): return g**(1/2)
def gen_I(): return sympy.eye(2)
def gen_Rx(theta): return sympy.exp(-sympy.I*theta/2*gen_X()).applyfunc(quantsimp)
def gen_Ry(theta): return sympy.exp(-sympy.I*theta/2*gen_Y()).applyfunc(quantsimp)
def gen_Rz(phi): return sympy.exp(-sympy.I*phi/2*gen_Z()).applyfunc(quantsimp)
def gen_GP(theta, qbits): return sympy.exp(theta*sympy.I)*sympy.eye(1<<qbits)
def gen_H(): return sympy.Matrix([[1, 1], [1, -1]])/sympy.sqrt(2)
def gen_X(): return sympy.Matrix([[0, 1], [1, 0]])
def gen_Y(): return sympy.Matrix([[0, -sympy.I], [sympy.I, 0]])
def gen_Z(): return sympy.Matrix([[1, 0], [0, -1]])
def gen_S(): return sympy.Matrix([[1, 0], [0, sympy.I]])
def gen_Sdg(): return make_inverse(gen_S()) #sympy.Matrix([[1, 0], [0, -sympy.I]])
def gen_SX(): return make_sqrt(gen_X()).applyfunc(quantsimp)
def gen_CZPowGate(t): return gen_CP(sympy.pi*t)
def gen_fSim(theta, phi): return compile_gates(2, [(gen_iSWAP_pow(-2*theta/sympy.pi), [0, 1]), (gen_CZPowGate(-phi/sympy.pi), [0, 1])])
def gen_SYC(): return gen_fSim(sympy.pi/2, sympy.pi/6)
def gen_T(): return sympy.Matrix([[1, 0], [0, sympy.exp(sympy.I*sympy.pi/4)]])
def gen_Tdg(): return make_inverse(gen_T())
def gen_P(theta): return sympy.Matrix([[1, 0], [0, sympy.exp(sympy.I*theta)]])
def gen_U1(theta): return gen_P(theta)
def gen_CH(): return sympy.Matrix(make_controlled(gen_H(), 1))
def gen_CX(): return sympy.Matrix(make_controlled(gen_X(), 1))
def gen_CNOT(): return gen_CX()
def gen_CY(): return sympy.Matrix(make_controlled(gen_Y(), 1))
def gen_CZ(): return sympy.Matrix(make_controlled(gen_Z(), 1))
def gen_U(theta, phi, lbda): return compile_gates(1, [(gen_Rz(phi), [0]), (gen_Ry(theta), [0]), (gen_Rz(lbda), [0]), (gen_GP((phi+lbda)/2, 1), [0])])
def gen_U2(phi, lbda): return gen_U(sympy.pi/2, phi, lbda)
def gen_U3(theta, phi, lbda): return gen_U(theta, phi, lbda)
def gen_R(theta, phi): return gen_U(theta, phi-sympy.pi/2, -phi+sympy.pi/2)
def gen_CR(theta, phi): return make_controlled(gen_R(theta, phi), 1)
def gen_CROT(theta, phi): return make_controlled(gen_R(theta, phi), 1, gen_R(-theta, phi))
def gen_CRX(theta): return make_controlled(gen_Rx(theta), 1)
def gen_CRY(theta): return make_controlled(gen_Ry(theta), 1)
def gen_CRZ(theta): return make_controlled(gen_Rz(theta), 1)
def gen_CCX(): return make_controlled(gen_CNOT(), 2)
def gen_Toffoli(): return gen_CCX()
def gen_CCZ(): return make_controlled(gen_CZ(), 2)
def gen_SWAP(): return functools.reduce(operator.add, (compile_gates(2, [(gen(), [0]), (gen(), [1])]) for gen in (gen_I, gen_X, gen_Y, gen_Z))) / 2
def gen_CSWAP(): return make_controlled(gen_SWAP(), 2)
def gen_iSWAP(): return gen_Rxy(-sympy.pi)
def gen_iSWAP_pow(alpha): return (gen_iSWAP()**alpha).applyfunc(quantsimprw)#.rewrite(sympy.exp)
def gen_CP(phi): return make_controlled(gen_P(phi), 1)
def gen_CR(phi): return gen_CP(phi)
def gen_CS(): return make_controlled(gen_S(), 1)
def gen_CU1(theta): return gen_CP(theta)
def gen_CU(theta, phi, lbda, gamma): return make_controlled(compile_gates(1, [(gen_U(theta, phi, lbda), [0]), (gen_GP(gamma, 1), [0])]), 1)
def gen_CU3(theta, phi, lbda): return gen_CU(theta, phi, lbda, 0)
def gen_Rxx(theta): return sympy.exp(-sympy.I*theta/2*compile_gates(2, [(gen_X(), [0]), (gen_X(), [1])])).applyfunc(quantsimp) #compile_gates(2, [(sympy.cos(theta/2)*gen_I(), [0]), (gen_I(), [1])]) - compile_gates(2, [(sympy.I*sympy.sin(theta/2)*gen_X(), [0]), (gen_X(), [1])])
def gen_Ryy(theta): return sympy.exp(-sympy.I*theta/2*compile_gates(2, [(gen_Y(), [0]), (gen_Y(), [1])])).applyfunc(quantsimp) #compile_gates(2, [(sympy.cos(theta/2)*gen_I(), [0]), (gen_I(), [1])]) - compile_gates(2, [(sympy.I*sympy.sin(theta/2)*gen_Y(), [0]), (gen_Y(), [1])])
def gen_Rzz(theta): return sympy.exp(-sympy.I*theta/2*compile_gates(2, [(gen_Z(), [0]), (gen_Z(), [1])])).applyfunc(quantsimp) #compile_gates(2, [(sympy.cos(theta/2)*gen_I(), [0]), (gen_I(), [1])]) - compile_gates(2, [(sympy.I*sympy.sin(theta/2)*gen_Z(), [0]), (gen_Z(), [1])])
def gen_Rxy(phi): return sympy.exp(-sympy.I*phi/4*(compile_gates(2, [(gen_X(), [0]), (gen_X(), [1])]) + compile_gates(2, [(gen_Y(), [0]), (gen_Y(), [1])]))).applyfunc(quantsimprw)

def gen_SX_test(): return sympy.Matrix([[1+sympy.I, 1-sympy.I], [1-sympy.I, 1+sympy.I]])/2
def gen_Rx_test(theta): return sympy.Matrix([[sympy.cos(theta/2), -sympy.I*sympy.sin(theta/2)], [-sympy.I*sympy.sin(theta/2), sympy.cos(theta/2)]])
def gen_SYC_test(): return sympy.Matrix([[1, 0, 0, 0], [0, 0, -sympy.I, 0], [0, -sympy.I, 0, 0], [0, 0, 0, sympy.exp(-sympy.I*sympy.pi/6)]])
assert gen_SX() == gen_SX_test()
assert gen_Rx(theta) == gen_Rx_test(theta)
assert gen_SYC() == gen_SYC_test()
qtheta, qphi, qlbda, qgamma, qalpha = Parameter("θ"), Parameter("ϕ"), Parameter("λ"), Parameter("γ"), Parameter("α")
def qiskit_U3(qtheta, qphi, qlbda): qc = QuantumCircuit(1); qc.u(qtheta, qphi, qlbda, 0); return qc
def qiskit_U3_decomp(qtheta, qphi, qlbda): qc = QuantumCircuit(1); qc.rz(qphi, 0); qc.ry(qtheta, 0); qc.rz(qlbda, 0); qc.append(GlobalPhaseGate((qphi+qlbda)/2)); return qc
def qiskit_CY(): qc = QuantumCircuit(2); qc.cy(0, 1); return qc
def qiskit_CY_decomp(): qc = QuantumCircuit(2); qc.h(1); qc.s(1); qc.cx(0, 1); qc.sdg(1); qc.h(1); return qc
def qiskit_CCX(): qc = QuantumCircuit(3); qc.ccx(0, 1, 2); return qc
def qiskit_CCX_decomp(): qc = QuantumCircuit(3); qc.h(2); qc.cx(1, 2); qc.tdg(2); qc.cx(0, 2); qc.t(2); qc.cx(1, 2); qc.tdg(2); qc.cx(0, 2); qc.t(1); qc.t(2); qc.h(2); qc.cx(0, 1); qc.t(0); qc.tdg(1); qc.cx(0, 1); return qc
def qiskit_CU(qtheta, qphi, qlbda, qgamma): qc = QuantumCircuit(2); qc.cu(qtheta, qphi, qlbda, qgamma, 0, 1); return qc
def qiskit_CU_decomp(qtheta, qphi, qlbda, qgamma): qc = QuantumCircuit(2); qc.rz((qphi-qlbda)/2, 1); qc.cx(0, 1); qc.rz(-(qphi+qlbda)/2, 1); qc.ry(-qtheta/2, 1); qc.cx(0, 1); qc.ry(qtheta/2, 1); qc.rz(qlbda, 1); qc.p((qlbda+qphi)/2+qgamma, 0); return qc
#print(gate_to_latex_matrix("U", (theta, phi, lbda), gen_U(theta, phi, lbda), [gen_Rz(phi), gen_Ry(theta), gen_Rz(lbda), gen_GP((phi+lbda)/2, 1)], [qiskit_U3(qtheta, qphi, qlbda), qiskit_U3_decomp(qtheta, qphi, qlbda)]))
#print(gate_to_latex_matrix("CY", (), gen_CY(), [], [qiskit_CY(), qiskit_CY_decomp()]))
#print(gate_to_latex_matrix("CU", (theta, phi, lbda, gamma), gen_CU(theta, phi, lbda, gamma), [], [qiskit_CU(qtheta, qphi, qlbda, qgamma), qiskit_CU_decomp(qtheta, qphi, qlbda, qgamma)]))
#print(gate_to_latex_matrix("CCX", (), gen_CCX(), [], [qiskit_CCX(), qiskit_CCX_decomp()]))

A `CY` gate, for example, can be decomposed with Hadamard `H` gates and `S` on the target, then the `CNOT`, followed by  `S` inverse called "S-dagger" or `Sdg`=$S^\dagger$ and `H` gates on the target.

In [ ]:
def gen_CY_decomp(): return compile_gates(2, [(gen_H(), [1]), (gen_S(), [1]), (gen_CNOT(), [0, 1]), (gen_Sdg(), [1]), (gen_H(), [1])])
assert gen_CY() == gen_CY_decomp()

### Exercise 2: Provide decompositions for `CZ`, `CRY` and `CRZ`

Hints:
`CZ` just requires X-axis and Z-axis flip on the target before and after the `CNOT` which is done with a Hadamard `H` gate.  
`CRY` can be done with 2 `CNOT`s but before the first `theta/2` Y-axis rotation is needed on the target, and between them `-theta/2`.  
Lastly `CRZ` can be done just like `CRY` but with Z-axis rotations instead of Y.


In [ ]:
# TODO: Modify the lists in the 3 functions below so the assertions pass.
def gen_CZ_decomp(): return compile_gates(2, [])
def gen_CRY_decomp(theta): return compile_gates(2, [])
def gen_CRZ_decomp(theta): return compile_gates(2, [])

if gen_CZ() != gen_CZ_decomp(): print("Not equal", gen_CZ(), gen_CZ_decomp())
elif gen_CRY(theta) != gen_CRY_decomp(theta): print("Not equal", gen_CRY(theta), gen_CRY_decomp(theta))
elif gen_CRZ(theta) != gen_CRZ_decomp(theta): print("Not equal", gen_CRZ(theta), gen_CRZ_decomp(theta))
else: print("All assertions passed!")

### Downloading and Importing QASM files

In [ ]:
qasm_url = "https://raw.githubusercontent.com/iic-jku/ibm_qx_mapping/refs/heads/master/examples/cnt3-5_179.qasm"
qasm_str = requests.get(qasm_url).text
qc3 = QuantumCircuit.from_qasm_str(qasm_str)
qc3.draw(output="text", fold=-1)

### Enumerating all partitions of a larger circuit.

In [ ]:
from squander import Qiskit_IO
from squander.partitioning.ilp import get_all_partitions
circ, parameters = Qiskit_IO.convert_Qiskit_to_Squander(qc3)
part_info = get_all_partitions(circ, max_qubits_per_partition=3)
"Circuit total gates:", len(circ.get_Gates()), "Circuit gate counts:", circ.get_Gate_Nums(), "Total partitions:", len(part_info[0]), "Partitions with gate indices:", part_info[0]


### Now we use the ILP solver to find the global minimal number of partitions.

In [ ]:
from squander.partitioning.ilp import max_partitions
from squander.partitioning.tools import translate_param_order
new_circ, new_param_order, L = max_partitions(circ, max_qubits_per_partition=3)
new_params = translate_param_order(parameters, new_param_order)
print("Partitions:", len(L), "Gates per partition:", [len(x) for x in L], "Partitions gate indexes:", L)
def squander_partitioned_to_qiskit(new_circ, new_params):
    qcpart = None
    for subcirc in new_circ.get_Gates():
        start = subcirc.get_Parameter_Start_Index()
        new_qc = Qiskit_IO.get_Qiskit_Circuit(subcirc, new_params[start:start+subcirc.get_Parameter_Num()])
        if qcpart is None: qcpart = new_qc
        else:
            qcpart.barrier()
            qcpart.compose(new_qc, inplace=True)
    return qcpart

qcpart = squander_partitioned_to_qiskit(new_circ, new_params)
qcpart.draw(output="text", fold=-1)

### Now we do the same again but using the fusion cost function.

In [ ]:
new_circ, new_param_order, L = max_partitions(circ, max_qubits_per_partition=3, fusion_cost=True)
new_params = translate_param_order(parameters, new_param_order)
print("Partitions:", len(L), "Gates per partition:", [len(x) for x in L], "Partitions gate indexes:", L)
qcpart = squander_partitioned_to_qiskit(new_circ, new_params)
qcpart.draw(output="text", fold=-1)

Check out the BSc thesis project which provides a visualization from end to SQUANDER [Qubitkit](https://qubit-mu.vercel.app/).

### Now we show the performance diffential between Qiskit and SQUANDER.

In [ ]:
initial_state = np.zeros(1<<new_circ.get_Qbit_Num(), dtype=np.complex128)
initial_state[0] = 1.0
import qiskit_aer as Aer
from qiskit import transpile
qcpart = Qiskit_IO.get_Qiskit_Circuit(new_circ.get_Flat_Circuit(), new_params)
squander_output = [None, None]
def run_squander():
    new_circ.set_min_fusion(14)
    transformed_state = initial_state.copy()
    def run():
        new_circ.apply_to(new_params, transformed_state)
        squander_output[0] = transformed_state
    squander_output[1] = run
qiskit_output = [None, None]
def run_qiskit():
    init = QuantumCircuit(qcpart.num_qubits)
    init.initialize( initial_state )
    qiskit_circuit = qcpart.compose(init, front=True)
    qiskit_circuit.save_statevector()
    backend = Aer.AerSimulator(method='statevector', fusion_enable=True, fusion_max_qubit=3)
    compiled_circuit = transpile(qiskit_circuit, backend)
    def run():
        result = backend.run(compiled_circuit).result()
        transformed_state = result.get_statevector(compiled_circuit)
        qiskit_output[0] = np.array(transformed_state)
    qiskit_output[1] = run

squander_prep_time = timeit.timeit(run_squander, number=1)
qiskit_prep_time = timeit.timeit(run_qiskit, number=1)
squander_run_time = timeit.timeit(squander_output[1], number=10)
qiskit_run_time = timeit.timeit(qiskit_output[1], number=10)
print(f"Squander prep time: {squander_prep_time:.4f}s, run time (10 iters): {squander_run_time:.4f}s")
print(f"Qiskit prep time: {qiskit_prep_time:.4f}s, run time (10 iters): {qiskit_run_time:.4f}s")

### Exercise 3: partition the famous 5-qubit Perfect Code Encoder into 3 and 4 qubit partitions with and without a fusion cost function

In [ ]:
def five_qubit_code_encoder():
    qc = QuantumCircuit(5, name="5Q Perfect Code Encoder")

    # Logical qubit is on qubit 0.
    # Qubits 1–4 are ancillas.

    # ---- Step 1: Spread state using Hadamards ----
    qc.h(2)
    qc.h(3)
    qc.h(4)

    # ---- Step 2: Entangle logical qubit with ancillas ----
    qc.cx(0, 1)
    qc.cx(0, 2)
    qc.cx(0, 3)
    qc.cx(0, 4)

    # ---- Step 3: Controlled-Z patterns for stabilizer structure ----
    qc.cz(1, 2)
    qc.cz(2, 3)
    qc.cz(3, 4)
    qc.cz(4, 1)

    # ---- Step 4: Additional entangling structure ----
    qc.cx(1, 0)
    qc.cx(2, 0)
    qc.cx(3, 0)
    qc.cx(4, 0)

    # ---- Step 5: Phase corrections ----
    qc.s(1)
    qc.s(2)
    qc.s(3)
    qc.s(4)

    # Final Hadamard layer for correct stabilizer alignment
    qc.h(1)
    qc.h(2)
    qc.h(3)
    qc.h(4)

    return qc
qc5 = five_qubit_code_encoder()
display(circuit_drawer(qc5, output="mpl"))
qc5, qc5params = Qiskit_IO.convert_Qiskit_to_Squander(qc5)
new_circ, new_param_order, L = max_partitions(qc5, max_qubits_per_partition=3, fusion_cost=True)
new_params = translate_param_order(qc5params, new_param_order)
print("Partitions:", len(L), "Gates per partition:", [len(x) for x in L], "Partitions gate indexes:", L)
qcpart5 = squander_partitioned_to_qiskit(new_circ, new_params)
fig5 = circuit_drawer(qcpart5, output="mpl", fold=-1)
svg_filename5 = "demo_5qubit_circuit.svg"
fig5.savefig(svg_filename5, format="svg", bbox_inches="tight")
print(f"Saved SVG to {svg_filename5}")
display(fig5)

Can we find a provable minimal CNOT counter-example for 3 qubit partitioning of a 4-qubit circuit where a naive greedy Kahn-style topological sort partitioning is worse than the global optimum obtained by ILP?  In general for an n-qubit circuit with k-qubit partitions, this is not a trivial problem.  It asks in effect where "list-scheduling" is suboptimal with our objective.  But it can be obtained by searching in depth order over all $n(n-1)/2$ which is $6$ for 4-qubits.  If there are $g$ gates, the complexity is then $O((n(n-1)/2)^g)$.

Can you perhaps predict the amount of gates or the exact solution?  Keep in mind Kahn is order dependent for the next gate, and if its not using a consistent tie breaker, may be inconsistent.  What happens with $n=5, k=4$?  Keep in mind, our partitioner splits non-connected components that have no dependencies to give a comparable and more true partitioning as is also done in most literature.  What about $n=5, k=3$?

In [ ]:
from squander import Circuit
from squander.partitioning.kahn import kahn_partition
def find_smallest_canonical(n, k):
    cnots = list(itertools.combinations(range(n), 2))
    curlevel = [[]]
    while True: #BFS
        nextlevel = []
        for level in curlevel:
            for cnot in cnots:
                newlevel = level + [cnot]
                circ = Circuit(n)
                for gate in newlevel:
                    circ.add_CNOT(gate[0], gate[1])
                kahn_circ, _, L_kahn = kahn_partition(circ, max_qubit=k)
                ilp_circ, _, L_ilp = max_partitions(circ, max_qubits_per_partition=k)
                if len(L_kahn) != len(L_ilp):
                    return kahn_circ, len(L_kahn), ilp_circ, len(L_ilp), circ
                nextlevel.append(newlevel)
        curlevel = nextlevel
kahn_circ, count_kahn, ilp_circ, count_ilp, circcanon = find_smallest_canonical(4, 3)
print("Kahn partitions:", count_kahn, "ILP partitions:", count_ilp)
print(f"Solution with {count_kahn} Kahn partitions and {count_ilp} ILP partitions and {len(circcanon.get_Gates())} gates:")
print(Qiskit_IO.get_Qiskit_Circuit(circcanon, []).draw(output="text"))
print("Kahn partitioning result:")
print(squander_partitioned_to_qiskit(kahn_circ, []).draw(output="text"))
print("ILP partitioning result:")
print(squander_partitioned_to_qiskit(ilp_circ, []).draw(output="text"))


## CNOT and GL(n, 2) exploration

In [ ]:
def enumerate_unordered_cnot_BFS(n: int, topology=None, use_gl=True):
    # Precompute unordered pairs
    topology = [(i, j) for i in range(n) for j in range(i+1, n)] if topology is None else topology
    prior_level_info = None
    while True:
        visited, seq_pairs_of, seq_dir_of, res = enumerate_unordered_cnot_BFS_level(n, topology, prior_level_info, use_gl=use_gl)
        if not res: break
        yield res
        prior_level_info = (visited, seq_pairs_of, seq_dir_of, list(x[0] for x in reversed(res)))

def canonical_prefix_ok(seq):
    m = len(seq)
    if m <= 1: return -1
    succ = {}
    indeg = {}
    last_on = {}
    for k in range(m):
        for q in seq[k]:
            if q in last_on:
                p = last_on[q]
                succ.setdefault(p, set()).add(k)
                indeg[k] = indeg.get(k, 0) + 1
            last_on[q] = k
    import heapq
    pq = [(seq[x], x) for x in range(m) if indeg.get(x, 0) == 0]
    heapq.heapify(pq)
    for pos in range(m):
        # Kahn's algorithm
        if len(pq) == 0: return pos #malformed (shouldn't happen)
        u = heapq.heappop(pq)
        if u[1] != pos: return pos #deviation: not canonical
        for v in succ.get(u[1], ()):
            indeg[v] -= 1
            if indeg[v] == 0: heapq.heappush(pq, (seq[v], v))
    return -1
def enumerate_unordered_cnot_BFS_level(n: int, topology=None, prior_level_info=None, use_gl=True):
    """
    Enumerate GL(n,2) states in increasing CNOT depth.
    Moves are *recorded* as unordered pairs (for your "structure" view)
    but each expansion tries both directions internally.

    Yields: (depth, A, seq_pairs, seq_directed)
    - depth: minimal number of CNOTs
    - A: packed matrix (tuple of n bit-rows)
    - seq_pairs: minimal-length sequence of unordered pairs that reaches A
    - seq_directed: a matching directed-move realization of seq_pairs
    """
    if prior_level_info is None:
        # Initial state
        start_key = tuple(1 << i for i in range(n))

        # Visited: we only need to mark states once (minimal depth)
        visited = {start_key}

        # We also keep *one* representative sequence per state (unordered + directed)
        seq_pairs_of = {start_key: []}
        seq_dir_of = {start_key: []}

        # Yield the root
        return visited, seq_pairs_of, seq_dir_of, [(start_key, [], [])]
    else:
        visited, seq_pairs_of, seq_dir_of, q = prior_level_info
    res = []
    new_seq_pairs_of = {}
    new_seq_dir_of = {}

    while q:
        A = q.pop()
        last_pairs = seq_pairs_of[A]
        last_dirs = seq_dir_of[A]
        for p in topology:
            if not use_gl:
                if len(last_pairs) >= 3 and all(p==x for x in last_pairs[-3:]): continue # avoid more than 3 repeated CNOTs
                if canonical_prefix_ok(last_pairs + [p]) >= 0: continue  # not canonical prefix
            # Try both directions, but record the *same* unordered step 'p'
            for mv in (p, (p[1], p[0])) if use_gl else (p,):
                #CNOT left
                if use_gl:
                    if mv[0] == mv[1]: B = A
                    else: B = list(A); B[mv[1]] ^= B[mv[0]]; B = tuple(B)

                    if B in visited: continue  # already discovered at minimal depth
                else: B = tuple(last_dirs + [p])

                visited.add(B)
                new_seq_pairs_of[B] = last_pairs + [p]
                new_seq_dir_of[B] = last_dirs + [mv]

                # Emit as soon as we discover the state (BFS → minimal depth)
                res.append((B, new_seq_pairs_of[B], new_seq_dir_of[B]))
    return visited, new_seq_pairs_of, new_seq_dir_of, res
def build_sequence(stop=5, ordered=True, use_gl=True):
    #https://oeis.org/A002884
    #unordered sequence: 1, 1, 4, 88, 9556, 4526605
    #unordered at 5 qubits: {0: 1, 1: 10, 2: 85, 3: 650, 4: 4475, 5: 27375, 6: 142499, 7: 580482, 8: 1501297, 9: 1738232, 10: 517884, 11: 13591, 12: 24}
    for i in range(2, stop+1):
        d = {}
        for z in enumerate_unordered_cnot_BFS(i, use_gl=use_gl):
            for x in (list if ordered else set)(tuple(x[1]) for x in z):
                d[len(x)] = d.get(len(x), 0) + 1
            if not use_gl and len(d) > 5: break
        print("Ordered:", ordered, "UseGL:", use_gl, "Number of circuits for", i, "qubits at each depth:", {x: d[x] for x in sorted(d)}, "Total circuits:", sum(d.values()))
for ordered, use_gl in itertools.product((True, False), repeat=2):
    build_sequence(4, ordered=ordered, use_gl=use_gl)

### Based on this, we can visually inspect all of the deepest circuits for 2-4 qubits.

In [ ]:
def draw_circs_of_size(qubits, size, ordered=True):
    all_circs = list(enumerate_unordered_cnot_BFS(qubits))
    found = set()
    for circ_level in all_circs:
        if len(circ_level[0][1]) != size: continue # only the largest ones
        for largest_circ in circ_level:
            if not ordered and frozenset(largest_circ[1]) in found: continue
            found.add(frozenset(largest_circ[1]))
            qcgl = QuantumCircuit(qubits)
            for cnots in largest_circ[2]:
                if ordered: qcgl.cx(cnots[0], cnots[1])
                else: qcgl.cz(cnots[0], cnots[1])
            print(qcgl.draw(output="text"))
draw_circs_of_size(2, 3)
draw_circs_of_size(3, 6)
draw_circs_of_size(4, 9)

Now let's do the same but unordered.  We will use the target/control qubit reversible CZ gate to be more visually accurate.

In [ ]:
draw_circs_of_size(3, 2, False)

### Entanglement measure via OSR.

In [ ]:
def build_osr_matrix(U, n, A):
    A = list(reversed(A))
    B = list(sorted(set(range(n)) - set(A), reverse=True))
    A, B = [n-1-q for q in A], [n-1-q for q in B]
    dA = 1 << len(A)
    dB = 1 << len(B)
    return U.reshape([2]*(2*n)).transpose(tuple(A) + tuple(t+n for t in A) + tuple(B) + tuple(t+n for t in B)).reshape(dA*dA, dB*dB)
def accumulate_grad_for_cut(U, G, Umat, VTmat, n, A): # qubits on A
    A = list(reversed(A))
    B = list(sorted(set(range(n)) - set(A), reverse=True))
    A, B = [n-1-q for q in A], [n-1-q for q in B]
    dyadic_idxs = [1 << k for k in range(len(G))]
    mat = np.array(G) * Umat[:,dyadic_idxs] @ VTmat[dyadic_idxs,:]  # reconstruct U from its dyadic decomposition
    revmap = [None]*(2*n)
    for i, x in enumerate(tuple(A) + tuple(t+n for t in A) + tuple(B) + tuple(t+n for t in B)):
        revmap[x] = i
    U += mat.reshape([2]*(2*n)).transpose(tuple(revmap)).reshape(*U.shape)
    return U
def numerical_rank_osr(M, Fnorm, tol=1e-10):
    s = np.linalg.svd(M, full_matrices=False, compute_uv=False) / Fnorm
    #print(s)
    return int(np.sum(s >= s[0]*tol)), s
def operator_schmidt_rank(U, n, A, Fnorm, tol=1e-10):
    return numerical_rank_osr(build_osr_matrix(U, n, A), Fnorm, tol)
def unique_cuts(n):
    import itertools
    """All nontrivial unordered bipartitions (no complements)."""
    qubits = tuple(range(n))
    for r in range(1, n//2 + 1):  # only up to half
        for S in itertools.combinations(qubits, r):
            if r < n - r:
                yield S
            else:  # r == n-r (only possible when n even): tie-break
                comp = tuple(q for q in qubits if q not in S)
                if S < comp:      # lexicographically smaller tuple wins
                    yield S
def get_circuit_from_pairs(qbit_num, pairs, finalizing=True):
    circ = Circuit(qbit_num)
    for pair in pairs:
        circ.add_U3(pair[0])
        circ.add_U3(pair[1])
        circ.add_CNOT(pair[0], pair[1])
    if finalizing:
        for qbit in range(qbit_num):
            circ.add_U3(qbit)
    return circ
def ceil_log2(x): return 0 if x == 0 else (x-1).bit_length()
def logsumexp_smoothmax(Lc, tau=1e-2):
    m = max(Lc)
    sum = 0.0
    for v in Lc: sum += np.exp((v - m)/tau)
    return tau * np.log(sum) + m

def dyadic_loss(S, max_dyadic, rho=0.9, tol=1e-4):
    tot_dyadic = ceil_log2(len(S))
    w = 1.0
    acc = 0.0
    for k in range(max_dyadic-1, -1, -1):
        if k < tot_dyadic:
            val = S[1 << k] - S[0] * tol
            acc += w * val * val
        w *= rho
    return acc
def avg_loss(cuts_S, rho=0.9):
    max_dyadic = ceil_log2(max(len(S) for S in cuts_S))
    total_loss = 0.0
    for S in cuts_S:
        total_loss += dyadic_loss(S, max_dyadic, rho)
    return total_loss / len(cuts_S)
# Aggregated cost over cuts: softmax (log-sum-exp) of per-cut dyadic losses
def cuts_softmax_dyadic_cost(cuts_S, rho=0.1, tau=1e-2):
    if tau <= 0.0: raise RuntimeError("tau must be > 0")
    Lc = []
    max_dyadic = ceil_log2(max(len(S) for S in cuts_S))
    for S in cuts_S:
        Lc.append(dyadic_loss(S, max_dyadic, rho))
    return logsumexp_smoothmax(Lc, tau)

# Gradient w.r.t. the singular values (diagonal of dL/dΣ):
def dyadic_loss_grad_diag(S, max_dyadic, Fnorm, rho=0.1, tol=1e-4):
    n = len(S)
    # c_k = rho^k / Mk  for k=1..n-1, then prefix sum C_j = sum_{k=1}^j c_k
    tot_dyadic = ceil_log2(n)
    grad = [0.0] * tot_dyadic
    w = 1.0
    for k in range(max_dyadic-1, -1, -1):
        if k < tot_dyadic:
            idx = 1 << k
            grad[k] = 2.0 * w * S[idx] * (1.0-tol) / Fnorm  #1-tol not needed if using stop-grad
        w *= rho                         # w = rho^k
    return grad
def cuts_avg_dyadic_grad(cuts_S, Fnorm, rho=0.1):
    C = len(cuts_S)
    max_dyadic = ceil_log2(max(len(S) for S in cuts_S))
    Lc = []
    for c in range(C):
        Lc.append(dyadic_loss_grad_diag(cuts_S[c], max_dyadic, Fnorm * C, rho))
    return Lc
# Gradient w.r.t. singular values (same length as S).
# Only dyadic positions (1,2,4,...) get nonzero entries; others are 0.
def cuts_softmax_tail_grad(cuts_S, Fnorm, rho=0.1, tau=1e-2):
    C = len(cuts_S)
    if C == 0: return []
    max_dyadic = ceil_log2(max(len(S) for S in cuts_S))
    # 1) per-cut losses
    Lc = [dyadic_loss(cuts_S[c], max_dyadic, rho) for c in range(C)]

    # 2) softmax weights w_c = exp((Lc - m)/tau) / Z
    m = max(Lc)
    w = [np.exp((Lc[c] - m)/tau) for c in range(C)]
    Z = np.sum(w)
    for c in range(C): w[c] /= (Z if Z > 0.0 else 1.0)

    # 3) dL/dS^{(c)} = w_c * dL_c/dS^{(c)}
    return [[v * w[c] for v in dyadic_loss_grad_diag(cuts_S[c], max_dyadic, Fnorm, rho)] for c in range(C)]

# Build M with build_osr_matrix, then SVD (econ) and grab top triplet.
def top_k_triplet_for_cut(U, # (N x N), row-major, N = 1<<q
    q,                  # number of qubits
    A,  # qubits on side A
    Fnorm            # e.g., sqrt(N)
    ):
    # 1) Build M for this cut
    M = build_osr_matrix(U, q, A)
    k = min(M.shape)

    # 2) SVD: M = U * diag(S) * VT  (VT = V^H)
    # Row-major API handles leading dims as col counts.
    res = np.linalg.svd(M, full_matrices=False, compute_uv=True)
    return res.S / Fnorm, res.U, res.Vh # normalized singular value
def get_deriv_osr_entanglement(matrix, use_cuts, use_softmax):
    qbit_num = len(matrix).bit_length()-1
    cuts = list(unique_cuts(qbit_num)) if len(use_cuts) == 0 else use_cuts
    Fnorm = np.sqrt(len(matrix))
    deriv = np.zeros(matrix.shape, dtype=complex)
    # Compute the derivative of the OSR entanglement cost function
    triplets = []
    allS = []
    for cut in cuts:
        # 1) top k triplet on the normalized reshape M_c
        S, Umat, VTmat = top_k_triplet_for_cut(matrix, qbit_num, cut, Fnorm)
        triplets.append(([], Umat, VTmat))
        allS.append(S)
    if use_softmax: allS = cuts_softmax_tail_grad(allS, Fnorm, 1.0)
    else: allS = cuts_avg_dyadic_grad(allS, Fnorm, 0.9)
    for i in range(len(cuts)):
        triplets[i] = (allS[i], triplets[i][1], triplets[i][2])
    for i in range(len(cuts)):
        G, Umat, VTmat = triplets[i]
        accumulate_grad_for_cut(deriv, G, Umat, VTmat, qbit_num, cuts[i])
    return deriv
# Compute grad component = Re Tr( A^† B ) for A = dL/dU, B = dU/dθ
# A and B are (rows x cols) with row-major leading dimension.
def real_trace_conj_dot(A, B):
    return np.sum(A.real * B.real + A.imag * B.imag) # Re Tr(A^† B)
def param_derivs(circ, Umtx, x):
    n = len(x)
    derivs = [None]*n
    for i in range(n):
        kind = i % 3
        if kind == 0: # d/dt:  ∂U/∂t = U(t+π/2, φ, λ)
            x_shift = x.copy()
            x_shift[i] += np.pi/2
            Ui = Umtx.copy()
            circ.apply_to(x_shift, Ui)
            derivs[i] = Ui
        else: # d/dφ or d/dλ: ∂U/∂p = 0.5*(U(p+π/2) - U(p-π/2))
            xp = x.copy(); xp[i] += np.pi/2
            xm = x.copy(); xm[i] -= np.pi/2
            Up = Umtx.copy()
            Um = Umtx.copy()
            circ.apply_to(xp, Up)
            circ.apply_to(xm, Um)
            derivs[i] = 0.5 * (Up - Um)
    return derivs

qca = QuantumCircuit(3, name="Ansatz3Q")
qca.u(Parameter("θ_0"), Parameter("ϕ_0"), Parameter("λ_0"), 0)
qca.u(Parameter("θ_1"), Parameter("ϕ_1"), Parameter("λ_1"), 1)
qca.cx(0, 1)
qca.u(Parameter("θ_2"), Parameter("ϕ_2"), Parameter("λ_2"), 1)
qca.u(Parameter("θ_3"), Parameter("ϕ_3"), Parameter("λ_3"), 2)
qca.cx(1, 2)
fig = qca.draw(output="mpl")
svg_filename = "demo_3qubit_ansatz.svg"
fig.savefig(svg_filename, format="svg", bbox_inches="tight")
print(f"Saved SVG to {svg_filename}")
display(fig)
qca.barrier()
qca.u(Parameter("θ_4"), Parameter("ϕ_4"), Parameter("λ_4"), 0)
qca.u(Parameter("θ_5"), Parameter("ϕ_5"), Parameter("λ_5"), 1)
qca.u(Parameter("θ_6"), Parameter("ϕ_6"), Parameter("λ_6"), 2)
fig = qca.draw(output="mpl")
svg_filename = "demo_3qubit_ansatz_finalizing.svg"
fig.savefig(svg_filename, format="svg", bbox_inches="tight")
print(f"Saved SVG to {svg_filename}")
display(fig)


Now we use SQUANDER and scipy to find improved decompositions for our large circuit.

In [ ]:
from squander import N_Qubit_Decomposition_custom
import scipy
def Run_Decomposition(decomp, qbit_num, pairs, inner_tol=1e-8, finalizing=True):
    circ = get_circuit_from_pairs(qbit_num, pairs, finalizing)
    decomp.set_Gate_Structure(circ)
    decomp.set_Optimized_Parameters(np.random.rand(decomp.get_Parameter_Num())*(2*np.pi))
    decomp.Start_Decomposition()
    if finalizing:
        params = decomp.get_Optimized_Parameters()
        err = decomp.Optimization_Problem(params)
        return err < inner_tol
def OSR_with_local_alignment(pairs, Umtx, qbit_num, cuts, Fnorm, tol, use_softmax, method="basinhopping"):
    if len(pairs) != 0:
        circ = get_circuit_from_pairs(qbit_num, pairs, False)
        def cost(x):
            U = Umtx.copy()
            circ.apply_to(x, U)
            S = [operator_schmidt_rank(U, qbit_num, cut, Fnorm, tol)[1] for cut in cuts]
            if use_softmax: return cuts_softmax_dyadic_cost(S, 1.0)
            else: return avg_loss(S)
        def jacobian(x):
            U = Umtx.copy()
            circ.apply_to(x, U)
            dL = get_deriv_osr_entanglement(U, cuts, use_softmax)
            return [real_trace_conj_dot(dL, deriv) for deriv in param_derivs(circ, Umtx, x)]
        if method == "differential_evolution":
            best = scipy.optimize.differential_evolution(cost, [ (0, 2*np.pi) for _ in range(circ.get_Parameter_Num()) ], maxiter=100, polish=False)
            best = scipy.optimize.minimize(cost, best.x, method='BFGS', jac=jacobian, options={'maxiter': 200})
        elif method == "dual_annealing":
            best = scipy.optimize.dual_annealing(cost, [ (0, 2*np.pi) for _ in range(circ.get_Parameter_Num()) ], maxiter=100, minimizer_kwargs={'jac': jacobian})
        elif method == "basinhopping":
            best = scipy.optimize.basinhopping(cost, np.random.rand(circ.get_Parameter_Num())*(2*np.pi), niter=50, stepsize=np.pi/2, minimizer_kwargs={'jac': jacobian})
        elif method == "BFGS":
            best = min([scipy.optimize.minimize(cost, np.random.rand(circ.get_Parameter_Num())*(2*np.pi), method='BFGS', jac=jacobian, options={'maxiter': 200}) for _ in range(10)], key=lambda r: r.fun)
        U = Umtx.copy()
        circ.apply_to(best.x, U)
    else: U = Umtx
    return [(ceil_log2(rank), s) for cut in cuts for rank, s in (operator_schmidt_rank(U, qbit_num, cut, Fnorm, tol),)]
def tree_search_CNOT_structure(circ, circ_params, use_softmax=False, method="basinhopping", beam_width=None, parallel=False):
    qbit_num = circ.get_Qbit_Num()
    max_depth = circ.get_Gate_Nums()['CNOT']-1
    Umtx = np.eye(1<<qbit_num, dtype=np.complex128)
    circ.apply_to(circ_params, Umtx)
    Umtx = Umtx.conj().T  # invert target unitary
    inner_tol = 1e-8
    decomp = N_Qubit_Decomposition_custom(Umtx, config={'tolerance': inner_tol}, accelerator_num=0)
    decomp.set_Verbose(0)
    topology = [(i, j) for i in range(qbit_num) for j in range(i+1, qbit_num)]
    B = beam_width # 8*len(topology)
    cuts = list(unique_cuts(qbit_num))
    tol = 1e-3
    Fnorm = np.sqrt(1<<qbit_num)
    prior_level_info = None
    from concurrent.futures import ProcessPoolExecutor
    for depth in range(max_depth+1):
        remaining = max_depth - depth
        visited, seq_pairs_of, seq_dir_of, res = enumerate_unordered_cnot_BFS_level(qbit_num, topology, prior_level_info, use_gl=False)
        nextprefixes = []
        candidate_paths = list(set(tuple(x[1]) for x in res))
        if parallel and len(candidate_paths) > 2: hscores = list(ProcessPoolExecutor().map(functools.partial(OSR_with_local_alignment, Umtx=Umtx, qbit_num=qbit_num, cuts=cuts, Fnorm=Fnorm, tol=tol, use_softmax=use_softmax, method=method), candidate_paths))
        else:
            hscores = [OSR_with_local_alignment(path, Umtx, qbit_num, cuts, Fnorm, tol=tol, use_softmax=use_softmax, method=method) for path in candidate_paths]
        for path, h in zip(candidate_paths, hscores):
            curh = None if len(path)==0 else prefixes[path[:-1]]
            #print(path, h)
            min_cnots = max((x[0] for x in h), default=0)
            if min_cnots == 0:
                for i in range(10):
                    if Run_Decomposition(decomp, qbit_num, path, inner_tol):
                        return decomp.get_Circuit(), decomp.get_Optimized_Parameters()
            if min_cnots > remaining: continue
            if not curh is None:
                if max((x[0] for x in curh), default=0) < min_cnots: continue
            nextprefixes.append((path, h))
        nextprefixes.sort(key=lambda t: (max((x[0] for x in t[1]), default=0), sum(x[0] for x in t[1]), sum(1-x[1][0]*x[1][0] for x in t[1])))
        prefixes = {x[0]: x[1] for x in nextprefixes[:B]}
        prior_level_info = (visited, seq_pairs_of, seq_dir_of, list(x[0] for x in reversed(res) if tuple(x[1]) in prefixes))
def decompose_circuit_with_tree_search(circ, parameters, max_qubits_per_partition=3, use_softmax=False, method="basinhopping", beam_width=None):
    new_circ, new_param_order, L = max_partitions(circ, max_qubits_per_partition=max_qubits_per_partition)
    new_params = translate_param_order(parameters, new_param_order)
    rescirc, resparams = Circuit(new_circ.get_Qbit_Num()), []
    for subcirc in new_circ.get_Gates():
        start = subcirc.get_Parameter_Start_Index()
        involved_qubits = subcirc.get_Qbits()
        remap = {x: i for i, x in enumerate(involved_qubits)}
        subcircremap = subcirc.Remap_Qbits(remap, len(involved_qubits))
        subcircparams = new_params[start:start+subcirc.get_Parameter_Num()]
        res = [None]
        def run_tree_search(): res[0] = tree_search_CNOT_structure(subcircremap, subcircparams, use_softmax=use_softmax, method=method, beam_width=beam_width)
        t = timeit.timeit(run_tree_search, number=1)
        res = res[0]
        print("Original subcircuit:", subcirc.get_Gate_Nums())
        print("--- %s seconds elapsed during tree search ---" % t)
        if res is not None:
            print("Decomposed subcircuit:", res[0].get_Gate_Nums())
            print("With parameters:", res[1])
            print(Qiskit_IO.get_Qiskit_Circuit(subcircremap, subcircparams).draw(output="text", fold=-1))
            print(Qiskit_IO.get_Qiskit_Circuit(res[0], res[1]).draw(output="text", fold=-1))
            Umat = np.eye(1<<len(involved_qubits), dtype=np.complex128)
            subcircremap.apply_to(subcircparams, Umat)
            Ucheck = np.eye(1<<len(involved_qubits), dtype=np.complex128)
            res[0].apply_to(res[1], Ucheck)
            print("Unitary difference norm:", np.linalg.norm(Umat - Ucheck))
            rescirc.add_Circuit(res[0].Remap_Qbits({i: involved_qubits[i] for i in range(len(involved_qubits))}, new_circ.get_Qbit_Num()))
            resparams.append(res[1])
        else:
            print("No improved decomposition found.")
            rescirc.add_Circuit(subcirc)
            resparams.append(subcircparams)
    return rescirc, np.concatenate(resparams)

decomp_circ, decompparams = decompose_circuit_with_tree_search(circ, parameters, method="dual_annealing", beam_width=4)
print("Original circuit:", circ.get_Gate_Nums())
print("Final decomposed circuit:", decomp_circ.get_Gate_Nums())

### Exercise 4: experiment with 3 vs 4 qubit partitions, softmax vs average, basin hopping, dual annealing, and differential evolution

In [ ]:
for max_qubits_per_partition in (3,):
    new_circ, new_param_order, L = max_partitions(circ, max_qubits_per_partition=max_qubits_per_partition)
    print([x.get_Gate_Nums().get('CNOT', 0) for x in new_circ.get_Gates()])
for max_qubits_per_partition, use_softmax, method in itertools.product((3,), (True, False), ("basinhopping", "differential_evolution", "dual_annealing", "BFGS")):
    new_circ, new_param_order, L = max_partitions(circ, max_qubits_per_partition=max_qubits_per_partition)
    new_params = translate_param_order(parameters, new_param_order)
    testcirc = next(x for x in new_circ.get_Gates() if x.get_Gate_Nums().get('CNOT', 0) == (5 if max_qubits_per_partition == 3 else 17))
    startidx = testcirc.get_Parameter_Start_Index()
    testparams = new_params[startidx:startidx+testcirc.get_Parameter_Num()]
    involved_qubits = testcirc.get_Qbits()
    remap = {x: i for i, x in enumerate(involved_qubits)}
    testcircremap = testcirc.Remap_Qbits(remap, len(involved_qubits))
    testcirccopy = Circuit(testcircremap.get_Qbit_Num())
    for gate in testcircremap.get_Gates():
        testcirccopy.add_Gate(gate)
    print(f"Testing decomposition on subcircuit with {testcirccopy.get_Gate_Nums().get('CNOT', 0)} CNOTs, max_qubits_per_partition={max_qubits_per_partition}, use_softmax={use_softmax}, method={method}")
    decomp_circ, decompparams = decompose_circuit_with_tree_search(testcirccopy, testparams, max_qubits_per_partition=max_qubits_per_partition, use_softmax=use_softmax, method=method, beam_width=4)

# Wrap-up

In this notebook, we:
- Visualized and exported 3-qubit circuits as SVG (for slides).
- Implemented a toy FLOP-based cost model and compared partitionings.
- Explored CNOT-only linear reversible maps in GL(3,2) using BFS by depth.
- Saw how topology (all-to-all vs line) affects minimal CNOT depth.
- Built an OSR matrix, computed singular values, and defined a simple entanglement cost.

Conceptually, these pieces mirror the lecture:
- ILP chooses partitions.
- We can attach different weights:
  - FLOPs + I/O penalty  → simulation / fusion.
  - Minimal CNOT count   → decomposition on arbitrary topologies.
  - OSR-based costs      → entanglement-aware optimization inside each block.